In [2]:
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots

In [3]:
file_path = 'TILL6022_Emission_Dataset.csv'
df = pd.read_csv(file_path, delimiter=',')
df

country           co2 sector        date
0          Brazil     96.802000  Power  2019-01-01
1           China  14059.663000  Power  2019-01-01
2       EU27 & UK   1871.582000  Power  2019-01-01
3          France     51.088000  Power  2019-01-01
4         Germany    316.449000  Power  2019-01-01
...           ...           ...    ...         ...
123448      WORLD  91161.002811  Total  2022-05-27
123449      WORLD  86966.674211  Total  2022-05-28
123450      WORLD  84261.503877  Total  2022-05-29
123451      WORLD  89027.980953  Total  2022-05-30
123452      WORLD  91340.922924  Total  2022-05-31

[123453 rows x 4 columns]

In [4]:
# filter dataset on Transport sectors: 'International Shipping' or 'International Aviation' or 'Domestic Aviation' or 'Ground Transport'
sectors = ['International Shipping', 'International Aviation', 'Domestic Aviation', 'Ground Transport']
Transport_Sector =  df[df.sector.isin(sectors)]
print(Transport_Sector.head())




         country          co2            sector        date
34916     Brazil   201.662612  Ground Transport  2019-01-01
34917      China  2521.742753  Ground Transport  2019-01-01
34918  EU27 & UK  1635.252733  Ground Transport  2019-01-01
34919     France   210.607774  Ground Transport  2019-01-01
34920    Germany   198.961962  Ground Transport  2019-01-01


In [5]:
# exclude 'WORLD' from dataframe



from calendar import month

from matplotlib import animation


Transport_not_World = Transport_Sector[Transport_Sector.country != 'WORLD'].groupby(['country', 'date']).sum()

#reset index for optimal dataset and split date into years

Transport_Total = Transport_not_World.reset_index(['country', 'date'])
Transport_Total[["year", "month", "day"]] = Transport_Total["date"].str.split("-", expand = True)
Transport_Total['Date2'] = '2019' + '-' + Transport_Total['month'].astype(str) + '-' + Transport_Total['day']

fig = go.Figure()
# add trace
Years = ['2019', '2020']
Countries = ['UK', 'US', 'China', 'EU27 & UK', 'France', 'Germany', 'India', 'Italy', 'Japan', 'Russia', 'Spain']
months = list(Transport_Total.month.unique())

for k in Countries:
    for i in Years:
        z = Transport_Total[(Transport_Total.country == k) & (Transport_Total.year == i)]
        lop = fig.add_trace(
                go.Scatter(x=list(z.Date2),
                        y=list(z.co2),
                        name= k + i,
                        visible =True))


list_updatemenus = []

for n, country in enumerate(Countries):
    visible = [False] * 2 * len(Countries)
    visible[2*n] = True
    visible[2*n + 1] = True
    temp_dict = dict(label = str(country),
                 method = 'update',
                 args = [{'visible': visible},
                         {'title': ('CO2 emissions comparison 2019 versus 2020 in %s'% country)}])
    list_updatemenus.append(temp_dict)


fig.update_layout(updatemenus=list([dict(buttons= list_updatemenus)]), xaxis_title = 'Date', yaxis_title = 'CO2 emissions x 1000 (ppm)', xaxis=dict(tickformat="%d-%B"))


fig.update_layout(
    updatemenus=[
        dict(
            direction="down",
            pad={"r": 10, "t": 10},
            showactive=True,
            x=0.15,
            xanchor="left",
            y=1.1,
            yanchor="top"
        )
    ]
)

fig.update_layout(
    xaxis=dict(
        rangeselector=dict(
            buttons=list([
                dict(count=1,
                     label="1m",
                     step="month",
                     stepmode="backward"),
                dict(count=6,
                     label="6m",
                     step="month",
                     stepmode="backward"),
                dict(step="all")
            ])
        ),
        rangeslider=dict(
            visible=True
        ),
        type="date"
    )
)



fig.update_layout(
    height = 800,
    width = 1200
)
                        
fig.show()

In [6]:
Transport_not_World = Transport_Sector[Transport_Sector.country != 'WORLD'].groupby(['country', 'date']).sum()


#reset index for optimal dataset and split date into years

Transport_Total = Transport_not_World.reset_index(['country', 'date'])
Transport_Total[["year", "month", "day"]] = Transport_Total["date"].str.split("-", expand = True)

# create dataframe for sector

Transport_Sector[["year", "month", "day"]] = Transport_Sector["date"].str.split("-", expand = True)
Transport_Sector['Date2'] = '2019' + '-' + Transport_Sector['month'].astype(str) + '-' + Transport_Sector['day']
Transport_Sector2 = Transport_Sector[(Transport_Sector.year == '2019') | (Transport_Sector.year == '2020')]

sectors = ['International Aviation', 'Domestic Aviation', 'Ground Transport']

fig = make_subplots(rows = 3, 
                    cols = 1,
                    subplot_titles = ('International Aviation', 'Domestic Aviation', 'Ground Transport'))

for k in Countries:
    for i in Years:
        Int_Av = Transport_Sector2[(Transport_Sector2.country == k) & (Transport_Sector2.year == i) & (Transport_Sector2.sector == 'International Aviation')]
        lop = fig.add_trace(
                go.Scatter(x=list(Int_Av.Date2),
                            y=list(Int_Av.co2),
                            name= 'International Aviation' + k + i,
                            visible =True), 1, 1)

for k in Countries:
    for i in Years:
        Do_Av = Transport_Sector2[(Transport_Sector2.country == k) & (Transport_Sector2.year == i) & (Transport_Sector2.sector == 'Domestic Aviation')]
        lop = fig.add_trace(
                go.Scatter(x=list(Do_Av.Date2),
                            y=list(Do_Av.co2),
                            name= 'Domestic Aviation' + k + i,
                            visible =True), 2, 1)

for k in Countries:
    for i in Years:
        Gr_Trans = Transport_Sector2[(Transport_Sector2.country == k) & (Transport_Sector2.year == i) & (Transport_Sector2.sector == 'Ground Transport')]
        lop = fig.add_trace(
                go.Scatter(x=list(Gr_Trans.Date2),
                            y=list(Gr_Trans.co2),
                            name= 'Ground Transport' + k + i,
                            visible =True), 3, 1)

fig.update_layout(
    height = 1000
)

list_updatemenus = []


for n, country in enumerate(Countries):
    visible = [False] * 2 * len(Countries)
    visible[2*n] = True
    visible[2*n + 1] = True
    temp_dict = dict(label = str(country),
                 method = 'update',
                 args = [{'visible': visible},
                         {'title': ('CO2 emissions comparison 2019 versus 2020 by sector in %s'% country)}])
    list_updatemenus.append(temp_dict)


fig.update_layout(updatemenus=list([dict(buttons= list_updatemenus)]), xaxis_title = 'Date', yaxis_title = 'CO2 emissions x 1000 (ppm)', xaxis=dict(tickformat="%d-%B"))

fig['layout']['yaxis2']['title']='CO2 emissions x 1000 (ppm)'
fig['layout']['yaxis3']['title']='CO2 emissions x 1000 (ppm)'
fig['layout']['xaxis2']['title']='Date'
fig['layout']['xaxis3']['title']='Date'

fig.update_layout(
    updatemenus=[
        dict(
            direction="down",
            pad={"r": 10, "t": 10},
            showactive=True,
            x=0.15,
            xanchor="left",
            y=1.08,
            yanchor="top"
        ),
    ]
)

fig.update_layout(
    xaxis=dict(
        rangeselector=dict(
            buttons=list([
                dict(count=1,
                     label="1m",
                     step="month",
                     stepmode="backward"),
                dict(count=6,
                     label="6m",
                     step="month",
                     stepmode="backward"),
                dict(step="all")
            ])
        ),
        rangeslider=dict(
            visible=True
        ),
        type="date"
    )
)

fig.update_xaxes(rangeslider_thickness = 0.05)


fig.show()

/var/folders/pv/ccj0k2pj15bblyxjv9vdt2y40000gn/T/ipykernel_23966/3204922578.py:11: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/var/folders/pv/ccj0k2pj15bblyxjv9vdt2y40000gn/T/ipykernel_23966/3204922578.py:11: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/var/folders/pv/ccj0k2pj15bblyxjv9vdt2y40000gn/T/ipykernel_23966/3204922578.py:11: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in th

In [27]:
Transport_not_World = Transport_Sector[Transport_Sector.country != 'WORLD'].groupby(['country', 'date']).sum()


#reset index for optimal dataset and split date into years

Transport_Total = Transport_not_World.reset_index(['country', 'date'])
Transport_Total[["year", "month", "day"]] = Transport_Total["date"].str.split("-", expand = True)

# create dataframe for sector

Transport_Sector[["year", "month", "day"]] = Transport_Sector["date"].str.split("-", expand = True)
Transport_Sector['Date2'] = '2019' + '-' + Transport_Sector['month'].astype(str) + '-' + Transport_Sector['day']
Transport_Sector2 = Transport_Sector[(Transport_Sector.year == '2019') | (Transport_Sector.year == '2020')]

Transport_not_World = Transport_Sector[Transport_Sector.country != 'WORLD'].groupby(['country', 'date']).sum()

#reset index for optimal dataset and split date into years

Transport_Total = Transport_not_World.reset_index(['country', 'date'])
Transport_Total[["year", "month", "day"]] = Transport_Total["date"].str.split("-", expand = True)
Transport_Total['Date2'] = '2019' + '-' + Transport_Total['month'].astype(str) + '-' + Transport_Total['day']

# add trace
Years = ['2019', '2020', '2021']
Countries = ['UK', 'US', 'China', 'EU27 & UK', 'France', 'Germany', 'India', 'Italy', 'Japan', 'Russia', 'Spain']
sectors = ['International Aviation', 'Domestic Aviation', 'Ground Transport']

fig = make_subplots(rows = 4, 
                    cols = 1,
                    subplot_titles = ('Total', 'International Aviation', 'Domestic Aviation', 'Ground Transport'))

for k in Countries:
    for i in Years:
        z = Transport_Total[(Transport_Total.country == k) & (Transport_Total.year == i)]
        Int_Av = Transport_Sector[(Transport_Sector.country == k) & (Transport_Sector.year == i) & (Transport_Sector.sector == 'International Aviation')]
        Do_Av = Transport_Sector[(Transport_Sector.country == k) & (Transport_Sector.year == i) & (Transport_Sector.sector == 'Domestic Aviation')]
        Gr_Trans = Transport_Sector[(Transport_Sector.country == k) & (Transport_Sector.year == i) & (Transport_Sector.sector == 'Ground Transport')]
        lop = fig.add_traces(
                    [
                    go.Scatter(x=list(z.Date2),
                        y=list(z.co2),
                        name= 'Total'+ k + i,
                        visible = True),        
                    go.Scatter(x=list(Int_Av.Date2),
                            y=list(Int_Av.co2),
                            name= 'International Aviation' + k + i,
                            visible = True),
                    go.Scatter(x=list(Do_Av.Date2),
                            y=list(Do_Av.co2),
                            name= 'Domestic Aviation' + k + i,
                            visible = True),
                    go.Scatter(x=list(Gr_Trans.Date2),
                            y=list(Gr_Trans.co2),
                            name= 'Ground Transport' + k + i,
                            visible = True)]
                , rows=list(range(1,5)), cols=[1,1,1,1]
                )
# for k in Countries:
#     for i in Years:
#         Int_Av = Transport_Sector2[(Transport_Sector2.country == k) & (Transport_Sector2.year == i) & (Transport_Sector2.sector == 'International Aviation')]
#         lop = fig.add_trace(
#                 go.Scatter(x=list(Int_Av.Date2),
#                             y=list(Int_Av.co2),
#                             name= 'International Aviation' + k + i,
#                             visible = False), 2, 1)

# for k in Countries:
#     for i in Years:
#         Do_Av = Transport_Sector2[(Transport_Sector2.country == k) & (Transport_Sector2.year == i) & (Transport_Sector2.sector == 'Domestic Aviation')]
#         lop = fig.add_trace(
#                 go.Scatter(x=list(Do_Av.Date2),
#                             y=list(Do_Av.co2),
#                             name= 'Domestic Aviation' + k + i,
#                             visible = False), 3, 1)

# for k in Countries:
#     for i in Years:
#         Gr_Trans = Transport_Sector2[(Transport_Sector2.country == k) & (Transport_Sector2.year == i) & (Transport_Sector2.sector == 'Ground Transport')]
#         lop = fig.add_trace(
#                 go.Scatter(x=list(Gr_Trans.Date2),
#                             y=list(Gr_Trans.co2),
#                             name= 'Ground Transport' + k + i,
#                             visible = False), 4, 1)

fig.update_layout(
    height = 1500
)

list_updatemenus = []


for n, country in enumerate(Countries):
    visible = 4*[False] * len(Years) * len(Countries)
    try:
        for x in range(4*len(Years)):
            visible[4*len(Years)*n + x] = True
    except IndexError:
        continue
    print(visible)
    temp_dict = dict(label = str(country),
                 method = 'update',
                 args = [{'visible': visible},
                         {'title': ('CO2 emissions comparison 2019 versus 2020 by sector in %s'% country)}])
    list_updatemenus.append(temp_dict)

fig.update_layout(
    updatemenus=[
        dict(
            direction="down",
            pad={"r": 10, "t": 10},
            showactive=True,
            x=0,
            xanchor="left",
            y=1.04,
            yanchor="top"
        ),
    ]
)

fig.update_layout(updatemenus=list([dict(buttons= list_updatemenus)]), xaxis_title = 'Date', yaxis_title = 'CO2 emissions x 1000 (ppm)')

fig.update_layout(title_text = 'CO2 emissions comparison 2019 versus 2020')

fig.update_layout(xaxis=dict(tickformat="%d-%B"),
                 xaxis2=dict(tickformat="%d-%B"),
                 xaxis3=dict(tickformat="%d-%B"),
                 xaxis4=dict(tickformat="%d-%B")
                 )

fig['layout']['yaxis2']['title']='CO2 emissions x 1000 (ppm)'
fig['layout']['yaxis3']['title']='CO2 emissions x 1000 (ppm)'
fig['layout']['yaxis4']['title']='CO2 emissions x 1000 (ppm)'
fig['layout']['xaxis2']['title']='Date'
fig['layout']['xaxis3']['title']='Date'
fig['layout']['xaxis4']['title']='Date'

fig.show()


/var/folders/pv/ccj0k2pj15bblyxjv9vdt2y40000gn/T/ipykernel_23966/619260451.py:11: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/var/folders/pv/ccj0k2pj15bblyxjv9vdt2y40000gn/T/ipykernel_23966/619260451.py:12: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



[True, True, True, True, True, True, True, True, True, True, True, True, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False, False]
[False, False, False, False, False, False, False, False, False, False, False, False, Tr

In [8]:
from statistics import mean
Transport_not_World = Transport_Sector[Transport_Sector.country != 'WORLD'].groupby(['country', 'date']).sum()


#reset index for optimal dataset and split date into years

Transport_Final = Transport_not_World.reset_index(['country', 'date'])
Transport_Final[["year", "month", "day"]] = Transport_Final["date"].str.split("-", expand = True)

# create dataframe for sector

Transport_Sector[["year", "month", "day"]] = Transport_Sector["date"].str.split("-", expand = True)
Transport_Sector['Date2'] = '2019' + '-' + Transport_Sector['month'].astype(str) + '-' + Transport_Sector['day']
Transport_Sector2 = Transport_Sector[(Transport_Sector.year == '2019') | (Transport_Sector.year == '2020')]

Transport_not_World = Transport_Sector[Transport_Sector.country != 'WORLD'].groupby(['country', 'date']).sum()

#reset index for optimal dataset and split date into years

Transport_Final = Transport_not_World.reset_index(['country', 'date'])
Transport_Final[["year", "month", "day"]] = Transport_Final["date"].str.split("-", expand = True)
Transport_Final['Date2'] = '2019' + '-' + Transport_Final['month'].astype(str) + '-' + Transport_Final['day']

# add trace
Years = ['2019', '2020']
Countries = ['UK', 'US', 'China', 'EU27 & UK', 'France', 'Germany', 'India', 'Italy', 'Japan', 'Russia', 'Spain']
sectors = ['International Aviation', 'Domestic Aviation', 'Ground Transport']


Delta_Country = []
Date_country = []
Date_country_max = []
Percentage_Delta = []
for k in Countries:
    # for i in Years:
    Delta_Total = Transport_Final[(Transport_Final.country == k) & (Transport_Final.year == '2020')]
    diff_list = []
    for d in range(len(Delta_Total)-1):
            Diff = abs(Delta_Total['co2'].iloc[d] - Delta_Total['co2'].iloc[d+1])
            Co2Value = Delta_Total['co2'].iloc[d-1]
            diff_list.append(Diff)
            Date_country.append(Delta_Total.iloc[d]['date'])
    Max_Diff = max(diff_list)
    percent_Delta = ("%g" % round((Max_Diff/Co2Value)*100,1))
    # print(Meanvalue)
    # print('This is the max diff:' , Max_Diff, k)
    index_maxvalue = diff_list.index(Max_Diff)
    # print("Date at which delta is max: ", Date_country[index_maxvalue])
    maxDATE = Date_country[index_maxvalue]
    Delta_Country.append(Max_Diff)
    Date_country_max.append(maxDATE)
    Percentage_Delta.append(percent_Delta)
# print(Delta_Country)

 
Delta_Country_Do = []
Date_country_Do = []
Date_country_max_Do = []
Percentage_Delta_Do = []
for k in Countries:
    # for i in Years:
    Do_Av = Transport_Sector2[(Transport_Sector2.country == k) & (Transport_Sector2.year == '2020') & (Transport_Sector2.sector == 'Domestic Aviation')]
    diff_list_Do = []
    for d in range(len(Do_Av)-1):
            Diff = abs(Do_Av['co2'].iloc[d] - Do_Av['co2'].iloc[d+1])
            Co2Value = Do_Av['co2'].iloc[d-1]
            diff_list_Do.append(Diff)
            Date_country_Do.append(Do_Av.iloc[d]['date'])
    Max_Diff_Do = max(diff_list_Do)
    percent_Delta_Do = round((Max_Diff_Do/Co2Value)*100,1)
    # print('This is the max diff:' , Max_Diff_Do, k)
    index_maxvalue_Do = diff_list_Do.index(Max_Diff_Do)
    maxDATE_Do = Date_country_Do[index_maxvalue_Do]
    Delta_Country_Do.append(Max_Diff_Do)
    Date_country_max_Do.append(maxDATE_Do)
    Percentage_Delta_Do.append(percent_Delta_Do)
# print(Delta_Country)

Delta_Country_Trans = []
Date_country_Trans = []
Date_country_max_Trans = []
Percentage_Delta_Trans = []
for k in Countries:
    # for i in Years:
    Gr_Trans = Transport_Sector2[(Transport_Sector2.country == k) & (Transport_Sector2.year == '2020') & (Transport_Sector2.sector == 'Ground Transport')]
    diff_list_Trans = []
    for d in range(len(Gr_Trans)-1):
            Diff = abs(Gr_Trans['co2'].iloc[d] - Gr_Trans['co2'].iloc[d+1])
            Co2Value_Trans = Gr_Trans['co2'].iloc[d-1]
            diff_list_Trans.append(Diff)
            Date_country_Trans.append(Gr_Trans.iloc[d]['date'])
    Max_Diff_Trans = max(diff_list_Trans)
    Percent_Delta_Trans = round((Max_Diff_Trans/Co2Value_Trans)*100, 1)
    # print('This is the max diff:' , Max_Diff_Trans, k)
    Delta_Country_Trans.append(Max_Diff_Trans)
    index_maxvalue_Trans = diff_list_Trans.index(Max_Diff_Trans)
    maxDATE_Trans = Date_country_Trans[index_maxvalue_Trans]
    Date_country_max_Trans.append(maxDATE_Trans)
    Percentage_Delta_Trans.append(Percent_Delta_Trans)
# print(Delta_Country)


Delta_Country_Int = []
Date_country_Int = []
Date_country_max_Int = []
Percentage_Delta_Int = []
for k in Countries:
    # for i in Years:
    Int_Av = Transport_Sector2[(Transport_Sector2.country == k) & (Transport_Sector2.year == '2020') & (Transport_Sector2.sector == 'International Aviation')]
    diff_list_Int = []
    for d in range(len(Int_Av)-1):
            Diff = abs(Int_Av['co2'].iloc[d] - Int_Av['co2'].iloc[d+1])
            Meanvalue_Int = mean(Int_Av['co2'])
            diff_list_Int.append(Diff)
            Date_country_Int.append(Int_Av.iloc[d]['date'])
    Max_Diff_Int = max(diff_list_Int)
    Percent_Delta_Int = round((Max_Diff_Int/Meanvalue_Int)*100, 1)
    Delta_Country_Int.append(Max_Diff_Int)
    index_maxvalue_Int = diff_list_Int.index(Max_Diff_Int)
    maxDATE_Int = Date_country_Int[index_maxvalue_Int]
    Date_country_max_Int.append(maxDATE_Int)
    Percentage_Delta_Int.append(Percent_Delta_Int)
# print(Delta_Country)

DeltaTable = pd.DataFrame(
    {'Country': Countries,
     'Biggest Delta 2020': Delta_Country,
     'Percentage biggest Delta 2020': Percentage_Delta,
     'Date biggest Delta 2020': Date_country_max,
     'Biggest Ground Transportation Delta 2020': Delta_Country_Trans,
     'Percentage biggest Ground Transportation Delta 2020': Percentage_Delta_Trans,
     'Date biggest Ground Transportation Delta 2020': Date_country_max_Trans,
     'Biggest Domestic Aviation Delta 2020': Delta_Country_Do,
     'Percentage biggest Domestic Aviation Delta 2020': Percentage_Delta_Do,
     'Date biggest Domestic Aviation Delta 2020': Date_country_max_Do,
     'Biggest International Aviation Delta 2020': Delta_Country_Int,
     'Percentage biggest International Aviation Delta 2020': Percentage_Delta_Int,
     'Date biggest International Aviation Delta 2020': Date_country_max_Int
    })

DeltaTable

import numpy as np 
import pandas as pd



DeltaTable.style.background_gradient(cmap='Blues')
# DeltaTable

/var/folders/pv/ccj0k2pj15bblyxjv9vdt2y40000gn/T/ipykernel_23966/1959779445.py:12: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/var/folders/pv/ccj0k2pj15bblyxjv9vdt2y40000gn/T/ipykernel_23966/1959779445.py:13: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

